In [102]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation
from IPython.display import HTML

# ============================================================
#  VECTORND (OPERACIONES BÁSICAS)
# ============================================================

class VectorND:
    def __init__(self, coords):
        self.coords = list(coords)

    def copy(self):
        return VectorND(self.coords[:])

    def __len__(self):
        return len(self.coords)

    def __getitem__(self, i):
        return self.coords[i]

    def __repr__(self):
        return f"VectorND({self.coords})"

    def __add__(self, other):
        return VectorND([a + b for a, b in zip(self.coords, other.coords)])

    def __sub__(self, other):
        return VectorND([a - b for a, b in zip(self.coords, other.coords)])

    def __mul__(self, scalar):
        return VectorND([scalar * c for c in self.coords])

    def __rmul__(self, scalar):
        return VectorND([scalar * c for c in self.coords])

In [103]:
# ============================================================
#  RUNGE–KUTTA ORDEN 4
# ============================================================

def rungeKutta(f, y0: VectorND, t0: float, T: float, steps: int, params: dict):
    h = (T - t0) / steps
    t = t0
    y = y0.copy()

    sol = [y.copy()]
    times = [t]

    for _ in range(steps):

        k1 = f(y, t, params)
        k2 = f(y + k1*(h/2), t + h/2, params)
        k3 = f(y + k2*(h/2), t + h/2, params)
        k4 = f(y + k3*h, t + h, params)

        y = y + (k1 + 2*k2 + 2*k3 + k4)*(h/6)
        t += h

        sol.append(y.copy())
        times.append(t)

    return sol, times

In [183]:
# ============================================================
#  POSICIÓN DE LA PARTÍCULA CONDUCIDA (Derecha extrema)
#  x_drive(t, n_dyn, a) posición inicial en x0 = n_dyn*a.
# ============================================================
def x_drive(t, n_dyn, a=1.0, vmax=50.0):
    x0 = n_dyn * a

    # Aceleración y frenado suave de la partícula conductora
    term1 = vmax * np.log(1 + np.exp(t - 2.0))
    term2 = -1.2 * vmax * np.log(1 + np.exp(t - 15.0))
    term3 = 2 * vmax * np.log(1 + np.exp(t - 22.0))

    #Función completa
    return x0 + term1 + term2 + term3

In [1]:
# ============================================================
#  DINÁMICA DE RESORTES ACOPLADOS (DERECHA CONDUCTORA)
#  y = [x1..x_{n-1}, p1..p_{n-1}]  (parte izquierda dinámica)
# ============================================================
def rhs(y: VectorND, t: float, params: dict) -> VectorND:
    """
    Campo vectorial derivado del Hamiltoniano de uns cadena de partículas unidas por resortes.
    H = Sum_0^n-1 (p_i²/2m + k/2(q_i+1 - q_i - a)²) + p_n/2m + (f(x) - q_n-1 - a)². Donde f(x) es la función de la partícula conductora.
    """
    n_total = params["n"]
    m = params["m"]
    k = params["k"]
    a = params["a"]  #Distancia entre partítuclas
    xdrv = params["x_drive"] #Función de la partícula conductora.

    n_dyn = n_total - 1  #Cadena de partículas sin contar la partícula conductora.

    x = y.coords[:n_dyn]   # x1 .. x_{n-1}
    p = y.coords[n_dyn:]   # p1 .. p_{n-1}

    dxdt = [0.0]*n_dyn
    dpdt = [0.0]*n_dyn

    # Velocidades
    for i in range(n_dyn):
        dxdt[i] = p[i] / m

    # Fuerzas
    for i in range(n_dyn):
        force = 0.0

        # resorte del vecino izquierdo (si existe)
        if i > 0:
            left = x[i-1]
            force += -k*(x[i] - left - a)

        # resorte del vecino derecho
        if i < n_dyn - 1:
            right = x[i+1]
            force += k*(right - x[i] - a)
        else:
            # partícula extrema derecha es conductora
            right = xdrv(t, n_dyn, a)
            force += k*(right - x[i] - a)

        dpdt[i] = force

    return VectorND(dxdt + dpdt)

NameError: name 'VectorND' is not defined

In [202]:
# ============================================================
#  PARÁMETROS E INICIALES
# ============================================================

params = {
    "n": 300,   # Número total de partículas
    "m": 1.0,
    "k": 100.0,
    "a": 5.0,
    "x_drive": x_drive
}

n_dyn = params["n"] - 1

# dinámica de las partículas incialmente en x = 0, a, 2a, ... (la partícula conductora es n_dyn*a)
x_init = [params["a"] * i for i in range(n_dyn)]
p_init = [0.0]*n_dyn

y0 = VectorND(x_init + p_init)

In [203]:
# ============================================================
#  INTEGRACIÓN NUMÉRICA
# ============================================================

T = 40
steps = 3000

sol, times = rungeKutta(rhs, y0, 0.0, T, steps, params)

In [190]:
# ============================================================
#  RECONSTRUIR POSICIONES COMPLETAS (dinámicas + conductora)
# ============================================================

def full_position(sol, times):
    """
    Devuelve la lista de las posiciones completas. Las calculadas con RK, y 
    la posición de la partícula conductora.
    """
    
    full_positions = []
    for yvec, t in zip(sol, times):
        x_dyn = yvec.coords[:n_dyn]
        full_positions.append(x_dyn + [params["x_drive"](t, n_dyn, params["a"])])

    full_positions = np.array(full_positions)
    t2 = np.array(times)

    return full_positions, t2


In [191]:
# ============================================================
#  FLUJO DE PARTÍCULAS A LA POSICIÓN X_GOAL
# ============================================================

def flux(positions, x_goal):
    """
    Mide la cantidad de elementos de una lista mayores a x_goal.
    """
    
    flujo = 0

    for pos in positions:
        if pos >= x_goal:
            flujo += 1

    return flujo

In [205]:
# ============================================================
#  SIMULACIÓN PARA DIFERENTES K
# ============================================================

#No ejecutar, simulación tardada.

i = 1
flujos = []

while i < 150:
    params["k"] = i
    sol, times = rungeKutta(rhs, y0, 0.0, T, steps, params)
    full_positions, t2 = full_position(sol, times)
    flujo = flux(full_positions[-1], 2500)
    flujos.append(flujo)
    i += 1


In [206]:
# ============================================================
#  COMPARACIÓN DE FLUJOS SEGÚN K
# ============================================================

print(flujos)

[13, 18, 21, 24, 27, 29, 31, 33, 35, 36, 38, 39, 40, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 52, 53, 54, 55, 56, 56, 57, 58, 58, 59, 60, 60, 61, 61, 62, 63, 63, 64, 64, 65, 65, 66, 66, 67, 67, 68, 68, 69, 69, 70, 70, 71, 71, 72, 72, 72, 73, 73, 74, 74, 74, 75, 75, 76, 76, 76, 77, 77, 77, 78, 78, 78, 79, 79, 80, 80, 80, 80, 81, 81, 81, 82, 82, 82, 83, 83, 83, 84, 84, 84, 84, 85, 85, 85, 86, 86, 86, 86, 87, 87, 87, 87, 88, 88, 88, 88, 89, 89, 89, 89, 90, 90, 90, 90, 91, 91, 91, 91, 92, 92, 92, 92, 93, 93, 93, 93, 93, 94, 94, 94, 94, 94, 95, 95, 95, 95, 95, 96, 96, 96, 96, 96, 97, 97, 97]


In [204]:
# ============================================================
#  ANIMACIÓN — ajuste automático de ejes y markersize
# ============================================================

full_positions, t2 = full_position(sol, times)

fig, ax = plt.subplots(figsize=(16, 5))

# set x-limits from simulated data with margin
xmin, xmax = full_positions.min(), full_positions.max()
ax.set_xlim(xmin, xmax)
ax.set_ylim(-0.5, 0.5)

points, = ax.plot([], [], 'o', markersize=4)

def init():
    points.set_data([], [])
    return points,

def update(frame):
    xdata = full_positions[frame]
    ydata = np.zeros_like(xdata)
    points.set_data(xdata, ydata)
    return points,

anim = FuncAnimation(fig, update, frames=range(0, len(t2), 7), init_func=init, interval=15)

plt.close(fig)
HTML(anim.to_jshtml())